In [1]:
#Import of the different modules needed

#Data Wrangling Module and Vizualisation
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import colorcet as cc
import random

#Bokeh Module
from bokeh.core.properties import Instance, Dict, JSON, Any, value
from bokeh.models import ColumnDataSource
from bokeh.models import GeoJSONDataSource
from bokeh.models import Select
from bokeh.models.widgets import TableColumn, DataTable
from bokeh.sampledata.sample_geojson import geojson
from bokeh.models import CategoricalColorMapper, ColorMapper, LogColorMapper, ContinuousColorMapper, LinearColorMapper
from bokeh.models import HoverTool, Tabs, Panel, CrosshairTool
from bokeh.palettes import Spectral10, viridis
from bokeh.plotting import figure
from bokeh.io import output_notebook, show, output_file
from bokeh.palettes import RdYlBu11 as palette, plasma
from bokeh.transform import factor_cmap, dodge
from bokeh.models import Range1d
from bokeh.models.widgets import RangeSlider, Dropdown
from bokeh.layouts import widgetbox, column

#Various Module : Geoloc + OS
import pandas
import geopandas as gpd
import os, sys

#Magic Command to see directly within the notebook
%matplotlib inline

In [2]:
#Lecture du fichier Shapefile en DataFrame via GeoPandas pour Dessiner la Carte Suisse
cwd = os.getcwd()
temp_cwd = cwd + '\\geo_data\\'
gdf0 = gpd.read_file(temp_cwd + 'gadm36_CHE_0.shp')
gdf1 = gpd.read_file(temp_cwd + 'gadm36_CHE_1.shp')

#Lecture fichier Shapefile en DataFrame via GeoPandas Pour les differentes Stations
gdf_loc_station = gpd.read_file('lorastation.shp', encoding = 'utf-8')
gdf_loc_station = gdf_loc_station.drop(20).reset_index(drop= True)

# Lecture fichier SHP de l'ensemble des lignes - Géolocalisation
gdf_loc_line = gpd.read_file('linie-mit-betriebspunkten.shp', encoding = 'utf-8')
gdf_loc_line = gdf_loc_line.sort_values(['linie', 'km']) #Tri pour dessiner les arrêts les uns après les autres.


In [3]:
# Lecture fichier Data_Passengers
data_passengers = pd.read_csv('passagierfrequenz.csv', sep=';',
                              engine='python', encoding = 'utf-8',
                              parse_dates=['Bezugsjahr'])

data_passengers['Year'] = data_passengers['Bezugsjahr'].astype(str).str[0:4].astype(float)

data_passengers = data_passengers.set_index('Bezugsjahr').drop(['Bemerkung', 'lod'], axis= 1).dropna(subset = ['geopos'])
data_passengers[['DTV', 'DMW']] = data_passengers[['DTV', 'DMW']].fillna(0)



In [4]:
connections = []
list_namelines = gdf_loc_line.linienname.unique().tolist()

for cities in list_namelines : 
    city = str(cities).split(' - ')
    connection = (city [0] +' -> ' + city[-1])
    connections.append(connection)

list_dd_menu = []

for i, line in enumerate(list_lines) : 
    l = str(line).split('.')[0]
    a = (l + ' - ' + connections[i],str(line))
    list_dd_menu.append(a)

list_dd_menu.append(('All', 'all'))

dd_menu = list_dd_menu
dropdown = Dropdown(label = 'Choose a Line', button_type = 'success' , menu = dd_menu)
show(dropdown)



NameError: name 'list_lines' is not defined

In [5]:
for i,elt in enumerate(dd_menu) :
    print(i, elt)

NameError: name 'dd_menu' is not defined

In [6]:
gdf_map

NameError: name 'gdf_map' is not defined

In [7]:
""" Création du DF juste pour les lignes de la suisse"""

gdf_loc_line = gdf_loc_line.drop(['lod', 'what3word_e','what3word_i', 'what3word_f', 'what3word_d'], axis = 1)

def getPointCoords(row, geom, coord_type):
    """Calculates coordinates ('x' or 'y') of a Point geometry"""
    if coord_type == 'x':
        return row[geom].x
    elif coord_type == 'y':
        return row[geom].y

# Calculate x coordinates
gdf_loc_line['x'] = gdf_loc_line.apply(getPointCoords, geom='geometry', coord_type='x', axis=1)

# Calculate y coordinates
gdf_loc_line['y'] = gdf_loc_line.apply(getPointCoords, geom='geometry', coord_type='y', axis=1)

list_df = []
list_x_coord = []
list_y_coord = []

list_lines = gdf_loc_line.linie.unique().tolist()

for i, linie in enumerate(list_lines) :
    df_line = gdf_loc_line[gdf_loc_line['linie'] == linie]
    a = df_line.x.tolist()
    list_x_coord.append(a)
    b = df_line.y.tolist()
    list_y_coord.append(b)

gdf_map = gdf_loc_line[['linie', 'linienname']].drop_duplicates().reset_index(drop = True)
serie_x_coord = pd.Series(list_x_coord)
serie_y_coord = pd.Series(list_y_coord)
gdf_map['x_coord'] = serie_x_coord
gdf_map['y_coord'] = serie_y_coord

In [45]:
#3er Onglet - Onglet de la carte suisse avec les Lignes de Trains.

list_lines = gdf_loc_line.linie.unique().tolist()
list_namelines = gdf_loc_line.linienname.unique().tolist()
source_geo = GeoJSONDataSource(geojson=gdf1.to_json())
source_geo_station = GeoJSONDataSource(geojson=gdf_loc_station.to_json())
source_geo_line = GeoJSONDataSource(geojson=gdf_loc_line.to_json())
source_map = ColumnDataSource(gdf_map)

output_notebook()

#Onglet Map

temp_f= figure(width = 1000, height = 1000, 
               title = 'Public Train Network Switzerland (SBB/CFF)')

temp_f.title.text_color = "black"
temp_f.title.text_font_style = "bold"


#Lecture du fichier Shapefile pour dessiner les contours du Pays.
temp_p1 = temp_f.patches('xs','ys', source = source_geo, line_color = 'black', fill_color = 'white')
temp_f.add_tools(HoverTool(renderers = [temp_p1], tooltips=[('Canton', '@NAME_1')]))

#Drawings of the Main Station - To make more accurate
temp_p2 = temp_f.circle('x','y', source = source_geo_station, 
                        color = 'gray',  size = 10,
                        alpha =0.60, legend = 'Main Station')    

#p_3 circle of every single stations
temp_p3 = temp_f.circle('x','y', source = source_geo_line, 
                        color = 'gray' , fill_color = 'white', 
                        size = 5, alpha = 0.80, legend ='Stations')

temp_p4 = temp_f.multi_line(xs = 'x_coord' , ys = 'y_coord', line_color = 'red', line_width=4, source = gdf_map)
temp_f.add_tools(CrosshairTool(),
                 HoverTool(renderers = [temp_p4], tooltips = [('Line', '@linie'),
                                                                ('Name Line', '@linienname')]))

"""
#Iteration de List_Line (Un DataFrame par ligne)
list_df = []
for i, linie in enumerate(list_lines) :
    new_df = gdf_loc_line[gdf_loc_line['linie'] == linie]
    list_df.append(new_df)
    temp_source = GeoJSONDataSource(geojson=new_df.to_json())
    temp_l = temp_f.line('x','y', source = temp_source, line_cap = 'round', line_width= 3, alpha = 0.70, color = 'red', hover_color='black')
    temp_f.add_tools(CrosshairTool(),
                     HoverTool(renderers = [temp_l], tooltips = [('Line', '@linie'),
                                                                ('Name Line', '@linienname'),
                                                                ('Company', '@verwaltung'),
                                                                ('Length (km)', '@km')]))

"""



    

    
    
temp_f.xgrid.grid_line_color = None
temp_f.ygrid.grid_line_color = None 

temp_f.xaxis.major_tick_line_color = None  # turn off x-axis major ticks
temp_f.xaxis.minor_tick_line_color = None  # turn off x-axis minor ticks
temp_f.yaxis.major_tick_line_color = None  # turn off y-axis major ticks
temp_f.yaxis.minor_tick_line_color = None  # turn off y-axis minor ticks
temp_f.xaxis.major_label_text_color = None  #note that this leaves space between the axis and the axis label  
temp_f.yaxis.major_label_text_color = None  #note that this leaves space between the axis and the axis label  

temp_f.outline_line_color = 'black'
temp_f.legend.location ='top_left'
    
"""Incorporation du menu DropDown"""
#Création du Menu
connections = []
for cities in list_namelines : 
    city = str(cities).split(' - ')
    connection = (city [0] +' -> ' + city[-1])
    connections.append(connection)


select_line = Select(title = 'Choose a Line', value = 'all', options = dd_menu)

#Fonction Callback pour relier le Menu Dropdown au plot


def callback_dd(attr, old, new) :
    if select_line.value == 'all' : 
        temp_source.data = temp_source.data
    else :
        for i, elt in enumerate (dd_menu) :
            if select_line.value == elt[1] :
                temp_source.data = ColumnDataSource(list_df[i]).data
select_line.on_change('value', callback_dd)
        
layout_onglet_map = column(select_line, temp_f)         

show(layout_onglet_map)

Loading BokehJS ...

You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    http://bokeh.pydata.org/en/latest/docs/user_guide/interaction/callbacks.html

Alternatively, to use real Python callbacks, a Bokeh server application may
be used. For more information on building and running Bokeh applications, see:

    http://bokeh.pydata.org/en/latest/docs/user_guide/server.html



In [46]:
#Onglet Données
from bokeh.layouts import row, column, gridplot
from bokeh.models.widgets import PreText

output_notebook()

gdf_loc_line_table = gdf_loc_line.drop('geometry', axis= 1)
source_table = ColumnDataSource(gdf_loc_line_table.sort_values(['bezeichnung']))

columns = [
        TableColumn(field = 'bezeichnung', title = 'Stopname', width = 140),
        TableColumn(field = 'linie', title = 'Lines n°', width = 80),
        TableColumn(field = 'linienname', title = 'Line Name', width = 200),
        TableColumn(field = 'km', title = 'Number of Km from Starting point', width = 100)
    ]

data_table = DataTable(source=source_table, columns=columns, height = 400, width = 900)


#Fin Table

#Table Passengers
source_table_passengers = ColumnDataSource(data_passengers)

from bokeh.models.widgets.tables import DateFormatter

columns_passengers = [
    TableColumn(field = 'Bezugsjahr', title = 'Date', formatter = DateFormatter(format = "%Y")),
    TableColumn(field = 'Code', title = 'Code'),
    TableColumn(field = 'Bahnhof_Haltestelle', title = 'Stop'),
    TableColumn(field = 'DTV', title = 'DTV'),
    TableColumn(field = 'DMW', title = 'DMW'),
    TableColumn(field = 'Eigner', title = 'Eigner'),
    TableColumn(field = 'geopos', title = 'GeoPos'),
                     ]

data_table_passengers = DataTable(source = source_table_passengers, columns = columns_passengers, index_header = 'Index', height = 400, width = 900)





pre1 = PreText(text="""Je peux écrire ce que je veux ici""", width=500, height=100)
pre2 = PreText(text="""JText numéro 2""", width=500, height=100)




column1 = column([select_line, data_table])
column2 = column([select_line, data_table_passengers])

layout = row(column1, column2)

show(layout)



Loading BokehJS ...

You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    http://bokeh.pydata.org/en/latest/docs/user_guide/interaction/callbacks.html

Alternatively, to use real Python callbacks, a Bokeh server application may
be used. For more information on building and running Bokeh applications, see:

    http://bokeh.pydata.org/en/latest/docs/user_guide/server.html



In [47]:
data_passengers_chart = data_passengers.drop(['geopos'], axis= 1)

data_passengers_2016 = data_passengers_chart[data_passengers_chart['Year'] == 2016 ].sort_values('Bahnhof_Haltestelle')
data_passengers_2014 = data_passengers_chart[data_passengers_chart['Year'] == 2014 ].sort_values('Bahnhof_Haltestelle')

data_passengers_2016 = data_passengers_2016.reset_index()

data_passengers_on_change = data_passengers_2016.drop('Bezugsjahr', axis= 1)

data_passengers_on_change['DTV_2016'] = data_passengers_on_change['DTV']
data_passengers_on_change['DMW_2016'] = data_passengers_on_change['DMW']

data_passengers_2014 = data_passengers_2014.reset_index()

data_passengers_on_change['Year_2014'] = data_passengers_2014['Year']
data_passengers_on_change['DTV_2014'] = data_passengers_2014['DTV']
data_passengers_on_change['DMW_2014'] = data_passengers_2014['DMW']

data_passengers_on_change = data_passengers_on_change.drop(['DTV', 'DMW'], axis = 1)

data_passengers_on_change

Code   Bahnhof_Haltestelle Eigner    Year  DTV_2016  DMW_2016  Year_2014  \
0      AD                Aadorf    SBB  2016.0    1700.0    2000.0     2014.0   
1      AA                 Aarau    SBB  2016.0   38000.0   44400.0     2014.0   
2     ABO     Aarburg-Oftringen    SBB  2016.0    2300.0    2700.0     2014.0   
3     AAT                Aathal    SBB  2016.0     690.0     750.0     2014.0   
4      AE                 Aesch    SBB  2016.0    1900.0    2200.0     2014.0   
5      AF    Affoltern am Albis    SBB  2016.0    6900.0    8100.0     2014.0   
6     AIG                 Aigle    CFF  2016.0    7600.0    8400.0     2014.0   
7      AI                Airolo    FFS  2016.0     550.0     490.0     2014.0   
8     ALL               Allaman    CFF  2016.0    3300.0    3900.0     2014.0   
9     ADF          Alpnach Dorf     ZB  2016.0    1500.0    1700.0     2014.0   
10    AST           Alpnachstad     ZB  2016.0     500.0     480.0     2014.0   
11     AL               Altdorf    SBB  2016.0     410.0     450.0     2014.0   
12   ALTD             Altendorf    SBB  2016.0     780.0     910.0     2014.0   
13     AT               Altmatt    SOB  2016.0      50.0      50.0     2014.0   
14    ALN                Altnau    SBB  2016.0     350.0     370.0     2014.0   
15    ALT         Altstätten SG    SBB  2016.0    2300.0    2600.0     2014.0   
16     AP          Ambri-Piotta    FFS  2016.0      50.0      50.0     2014.0   
17     AW              Amriswil    SBB  2016.0    3000.0    3400.0     2014.0   
18     AN           Andelfingen    SBB  2016.0    2300.0    2600.0     2014.0   
19    ARB                 Arbon    SBB  2016.0    1500.0    1700.0     2014.0   
20   ARBS     Arbon Seemoosriet    SBB  2016.0     410.0     460.0     2014.0   
21    ARD                 Ardon    CFF  2016.0     470.0     580.0     2014.0   
22    ARN                Arnegg    SBB  2016.0       0.0       0.0     2014.0   
23     AX                 Arnex    CFF  2016.0     200.0     230.0     2014.0   
24     GD           Arth-Goldau    SBB  2016.0   12600.0   12800.0     2014.0   
25   AUSG                 Au SG    SBB  2016.0     320.0     360.0     2014.0   
26     AU                 Au ZH    SBB  2016.0    1000.0    1200.0     2014.0   
27    AUV             Auvernier    CFF  2016.0     410.0     450.0     2014.0   
28     AV              Avenches    CFF  2016.0     710.0     830.0     2014.0   
29    BAA                  Baar    SBB  2016.0    8300.0    9800.0     2014.0   
..    ...                   ...    ...     ...       ...       ...        ...   
733  WUER              Würenlos    SBB  2016.0     920.0    1100.0     2014.0   
734   CHP  Yverdon-Champ Pittet    CFF  2016.0      50.0      60.0     2014.0   
735    YV     Yverdon-les-Bains    CFF  2016.0   16100.0   18900.0     2014.0   
736   YND               Yvonand    CFF  2016.0     620.0     730.0     2014.0   
737    ZB          Ziegelbrücke    SBB  2016.0    8900.0    9600.0     2014.0   
738   ZIM               Zimeysa    CFF  2016.0     930.0    1300.0     2014.0   
739    ZF              Zofingen    SBB  2016.0    8700.0   10100.0     2014.0   
740    ZK              Zollikon    SBB  2016.0    1100.0    1300.0     2014.0   
741    ZG                   Zug    SBB  2016.0   37500.0   43800.0     2014.0   
742  ZGCA            Zug Casino    SBB  2016.0     150.0     180.0     2014.0   
743  KMUE       Zug Chollermüli    SBB  2016.0     630.0     700.0     2014.0   
744  ZGFR          Zug Fridbach    SBB  2016.0     240.0     280.0     2014.0   
745   ZGO           Zug Oberwil    SBB  2016.0     250.0     280.0     2014.0   
746  ZGPP         Zug Postplatz    SBB  2016.0     140.0     160.0     2014.0   
747  ZGSE       Zug Schutzengel    SBB  2016.0    1200.0    1300.0     2014.0   
748   ZWD              Zweidlen    SBB  2016.0       0.0       0.0     2014.0   
749   ZWG               Zwingen    SBB  2016.0    2400.0    2800.0     2014.0   
750   ZAF      Zürich Affoltern    S

In [48]:
# Onglet Graphique 


#Chargement de la ColumnDataSource (Spécifique à Bokeh)
source_pass = ColumnDataSource(data_passengers_on_change)

output_notebook()

#Figure Does not plot if Duplicates in list 'Stops' - Need to drop Series with Unique.tolist()

fig_hbar = figure(x_range = (0, max(data_passengers_on_change['DMW_2016']) + 50000),
           y_range = data_passengers_on_change['Bahnhof_Haltestelle'].sort_values(ascending = False),
           plot_height = 10000, plot_width=2000,
           title = 'Passenger per Station')


p_hbar1 = fig_hbar.hbar(y=dodge('Bahnhof_Haltestelle', +0.20, range = fig_hbar.y_range) , right = 'DTV_2014',
              source = source_pass,  
              height = 0.20,
              color="#718dbf", legend=value("DTV 2014"))

p_hbar3 = fig_hbar.hbar(y=dodge('Bahnhof_Haltestelle', +0.10, range = fig_hbar.y_range) , right = 'DMW_2014',
              source = source_pass,  
              height = 0.20,
              color="lightblue", legend=value("DMW 2014"))

p_hbar2 = fig_hbar.hbar(y=dodge('Bahnhof_Haltestelle', -0.10, range = fig_hbar.y_range) , right = 'DTV_2016',
              source = source_pass,  
              height = 0.20,
              color="#e84d60", legend=value("DTV 2016"))

p_hbar4 = fig_hbar.hbar(y=dodge('Bahnhof_Haltestelle', -0.20, range = fig_hbar.y_range) , right = 'DMW_2016',
              source = source_pass,  
              height = 0.20,
              color="pink", legend=value("DMW 2016"))

fig_hbar.add_tools(HoverTool(renderers = [p_hbar1], tooltips = [('DTV_2014', '@DTV_2014'),
                                                   ('Station', '@Bahnhof_Haltestelle')]))

fig_hbar.add_tools(HoverTool(renderers = [p_hbar3], tooltips = [('DMW_2014', '@DMW_2014'),
                                                   ('Station', '@Bahnhof_Haltestelle')]))

fig_hbar.add_tools(HoverTool(renderers = [p_hbar2], tooltips = [('DTV_2016', '@DTV_2016'),
                                                   ('Station', '@Bahnhof_Haltestelle')]))

fig_hbar.add_tools(HoverTool(renderers = [p_hbar4], tooltips = [('DMW_2016', '@DMW_2016'),
                                                   ('Station', '@Bahnhof_Haltestelle')]))


fig_hbar.xaxis[0].formatter.use_scientific = False
fig_hbar.ygrid.grid_line_color = None
fig_hbar.legend.location = "top_right"
fig_hbar.legend.orientation = "horizontal"


menu = Select(options=['Toutes', 'Top 10', 'Top 20'], value='Toutes', title='Nombres de Villes')
range_slider = RangeSlider(start=0, end=200000, value=(1,200000), step=10000, title="Stuff")

def callback(attr, old, new):
    if menu.value == 'Toutes' : 
        source_pass.data = ColumnDataSource(data_passengers_on_change).data
        fig_hbar.x_range.start = 0
        fig_hbar.x_range.end = (max(data_passengers_on_change['DMW_2016']) + 50000)
    elif menu.value == 'Top 10':
        source_pass.data = ColumnDataSource(top_10_DMW16).data
        fig_hbar.x_range.start = 0
        fig_hbar.x_range.end = 20000
        fig_hbar.y_range.factors = top_10_DMW16['Bahnhof_Haltestelle']
    elif menu.value == 'Top 20' : 
        source_pass.data = ColumnDataSource(top_20_DMW16).data
        fig_hbar.y_range.factors = data_passengers_on_change['Bahnhof_Haltestelle'].sort_values(ascending = True)
        


menu.on_change('value', callback)

range_slider = RangeSlider(start=0, end=200000, value=(1,200000), step=10000, title="Stuff")


# Arrange plots and widgets in layouts
layout_2 = column(menu, range_slider, fig_hbar)
    
show(layout_2)


Loading BokehJS ...

You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    http://bokeh.pydata.org/en/latest/docs/user_guide/interaction/callbacks.html

Alternatively, to use real Python callbacks, a Bokeh server application may
be used. For more information on building and running Bokeh applications, see:

    http://bokeh.pydata.org/en/latest/docs/user_guide/server.html



In [52]:
""" Compilation de nos trois Onglets / 
    onglet_1 : nos données
    onglet 2 : fig_hbar : Histogramme Horizontal
    Onglet 3 : La map de suisse"""

onglet_1 = Panel(child = layout, title="Data")
onglet_2 = Panel(child = fig_hbar, title = "Data Visualisation")
onglet_3 = Panel(child = temp_f, title = "Swiss Map")

tabs = Tabs(tabs=[onglet_1, onglet_2, onglet_3])

show(tabs)


You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    http://bokeh.pydata.org/en/latest/docs/user_guide/interaction/callbacks.html

Alternatively, to use real Python callbacks, a Bokeh server application may
be used. For more information on building and running Bokeh applications, see:

    http://bokeh.pydata.org/en/latest/docs/user_guide/server.html



In [53]:
data_150000 = data_passengers_on_change[data_passengers_on_change['DTV_2016'] >= 150000]
data_5300 = data_passengers_on_change[data_passengers_on_change['DTV_2016'] >= 5300]
data_0_10000 = data_passengers_on_change[data_passengers_on_change['DTV_2016'] < 10000]

data_40000 =  data_passengers_on_change[data_passengers_on_change['DTV_2016'] < 40000]
data_40000

Code   Bahnhof_Haltestelle Eigner    Year  DTV_2016  DMW_2016  Year_2014  \
0      AD                Aadorf    SBB  2016.0    1700.0    2000.0     2014.0   
1      AA                 Aarau    SBB  2016.0   38000.0   44400.0     2014.0   
2     ABO     Aarburg-Oftringen    SBB  2016.0    2300.0    2700.0     2014.0   
3     AAT                Aathal    SBB  2016.0     690.0     750.0     2014.0   
4      AE                 Aesch    SBB  2016.0    1900.0    2200.0     2014.0   
5      AF    Affoltern am Albis    SBB  2016.0    6900.0    8100.0     2014.0   
6     AIG                 Aigle    CFF  2016.0    7600.0    8400.0     2014.0   
7      AI                Airolo    FFS  2016.0     550.0     490.0     2014.0   
8     ALL               Allaman    CFF  2016.0    3300.0    3900.0     2014.0   
9     ADF          Alpnach Dorf     ZB  2016.0    1500.0    1700.0     2014.0   
10    AST           Alpnachstad     ZB  2016.0     500.0     480.0     2014.0   
11     AL               Altdorf    SBB  2016.0     410.0     450.0     2014.0   
12   ALTD             Altendorf    SBB  2016.0     780.0     910.0     2014.0   
13     AT               Altmatt    SOB  2016.0      50.0      50.0     2014.0   
14    ALN                Altnau    SBB  2016.0     350.0     370.0     2014.0   
15    ALT         Altstätten SG    SBB  2016.0    2300.0    2600.0     2014.0   
16     AP          Ambri-Piotta    FFS  2016.0      50.0      50.0     2014.0   
17     AW              Amriswil    SBB  2016.0    3000.0    3400.0     2014.0   
18     AN           Andelfingen    SBB  2016.0    2300.0    2600.0     2014.0   
19    ARB                 Arbon    SBB  2016.0    1500.0    1700.0     2014.0   
20   ARBS     Arbon Seemoosriet    SBB  2016.0     410.0     460.0     2014.0   
21    ARD                 Ardon    CFF  2016.0     470.0     580.0     2014.0   
22    ARN                Arnegg    SBB  2016.0       0.0       0.0     2014.0   
23     AX                 Arnex    CFF  2016.0     200.0     230.0     2014.0   
24     GD           Arth-Goldau    SBB  2016.0   12600.0   12800.0     2014.0   
25   AUSG                 Au SG    SBB  2016.0     320.0     360.0     2014.0   
26     AU                 Au ZH    SBB  2016.0    1000.0    1200.0     2014.0   
27    AUV             Auvernier    CFF  2016.0     410.0     450.0     2014.0   
28     AV              Avenches    CFF  2016.0     710.0     830.0     2014.0   
29    BAA                  Baar    SBB  2016.0    8300.0    9800.0     2014.0   
..    ...                   ...    ...     ...       ...       ...        ...   
728    WO                Wohlen    SBB  2016.0    5300.0    6400.0     2014.0   
729   WOS       Wolfenschiessen     ZB  2016.0     420.0     460.0     2014.0   
730   WOL              Wollerau    SOB  2016.0     560.0     640.0     2014.0   
731    WY               Wynigen    SBB  2016.0     870.0    1000.0     2014.0   
732   WAE             Wädenswil    SBB  2016.0   16600.0   18900.0     2014.0   
733  WUER              Würenlos    SBB  2016.0     920.0    1100.0     2014.0   
734   CHP  Yverdon-Champ Pittet    CFF  2016.0      50.0      60.0     2014.0   
735    YV     Yverdon-les-Bains    CFF  2016.0   16100.0   18900.0     2014.0   
736   YND               Yvonand    CFF  2016.0     620.0     730.0     2014.0   
737    ZB          Ziegelbrücke    SBB  2016.0    8900.0    9600.0     2014.0   
738   ZIM               Zimeysa    CFF  2016.0     930.0    1300.0     2014.0   
739    ZF              Zofingen    SBB  2016.0    8700.0   10100.0     2014.0   
740    ZK              Zollikon    SBB  2016.0    1100.0    1300.0     2014.0   
741    ZG                   Zug    SBB  2016.0   37500.0   43800.0     2014.0   
742  ZGCA            Zug Casino    SBB  2016.0     150.0     180.0     2014.0   
743  KMUE       Zug Chollermüli    SBB  2016.0     630.0     700.0     2014.0   
744  ZGFR          Zug Fridbach    SBB  2016.0     240.0     280.0     2014.0   
745   ZGO           Zug Oberwil    S

In [54]:
data_40000.sort_values('DMW_2016',ascending = False)['Bahnhof_Haltestelle']

1                      Aarau
741                      Zug
751        Zürich Altstetten
34                     Baden
660                     Thun
678                    Uster
713                 Wetzikon
448                Neuchâtel
227        Fribourg/Freiburg
359                 Lenzburg
646                Stettbach
124                     Chur
90                  Brugg AG
688                    Vevey
168                 Dietikon
715                      Wil
509               Rapperswil
518                Renens VD
466                     Nyon
421                   Morges
575             Schaffhausen
697                     Visp
368                  Liestal
659                  Thalwil
185               Effretikon
732                Wädenswil
735        Yverdon-les-Bains
752              Zürich Enge
419                 Montreux
100                 Burgdorf
               ...          
325                Krummenau
593           Sennhof-Kyburg
606               Sitterdorf
367           

In [55]:
top_AZ = data_passengers_on_change.sort_values('Bahnhof_Haltestelle')


top_10_DMW16 = data_passengers_on_change.sort_values('DMW_2016', ascending = False).iloc[0:10]
top_10_DMW16_rev = top_10_DMW16.sort_values('DMW_2016', ascending = True).iloc[0:10]

top_20_DMW16 = data_passengers_on_change.sort_values('DMW_2016', ascending = False).iloc[0:20]
top_20_DMW16_rev = data_passengers_on_change.sort_values('DMW_2016', ascending = True).iloc[0:20]

top_50_DMW16 = data_passengers_on_change.sort_values('DMW_2016', ascending = False).iloc[0:50]

top_100_DMW16 = data_passengers_on_change.sort_values('DMW_2016', ascending = False).iloc[0:10]

top_500_DMW16 = data_passengers_on_change.sort_values('DMW_2016', ascending = False).iloc[0:500]


top_10_DMW14 = data_passengers_on_change.sort_values('DMW_2014', ascending = False).iloc[0:10]

top_20_DMW14 = data_passengers_on_change.sort_values('DMW_2014', ascending = False).iloc[0:20]

top_50_DMW14 = data_passengers_on_change.sort_values('DMW_2014', ascending = False).iloc[0:50]

top_100_DMW14 = data_passengers_on_change.sort_values('DMW_2014', ascending = False).iloc[0:10]

top_500_DMW14 = data_passengers_on_change.sort_values('DMW_2014', ascending = False).iloc[0:500]




top_10_DMW16_rev

Code Bahnhof_Haltestelle Eigner    Year  DTV_2016  DMW_2016  Year_2014  \
234    GE              Genève    CFF  2016.0   63400.0   73700.0     2014.0   
481    OL               Olten    SBB  2016.0   72700.0   81300.0     2014.0   
758  ZSTH  Zürich Stadelhofen    SBB  2016.0   71200.0   83300.0     2014.0   
756  ZOER     Zürich Oerlikon    SBB  2016.0   72400.0   85700.0     2014.0   
383    LZ              Luzern    SBB  2016.0   89200.0   96200.0     2014.0   
720     W          Winterthur    SBB  2016.0   94300.0  108000.0     2014.0   
349    LS            Lausanne    CFF  2016.0   95900.0  108900.0     2014.0   
40     BS           Basel SBB    SBB  2016.0  102700.0  114200.0     2014.0   
55     BN                Bern    SBB  2016.0  188100.0  210000.0     2014.0   
754   ZUE           Zürich HB    SBB  2016.0  420700.0  466800.0     2014.0   

     DTV_2014  DMW_2014  
234   60500.0   70700.0  
481   69300.0   78100.0  
758   68100.0   81100.0  
756   70900.0   84500.0  
383   84700.0   91800.0  
720   91500.0  105200.0  
349   94100.0  107100.0  
40   101400.0  112900.0  
55   180700.0  202600.0  
754  396300.0  441400.0

In [56]:
data_passengers_on_change

Code   Bahnhof_Haltestelle Eigner    Year  DTV_2016  DMW_2016  Year_2014  \
0      AD                Aadorf    SBB  2016.0    1700.0    2000.0     2014.0   
1      AA                 Aarau    SBB  2016.0   38000.0   44400.0     2014.0   
2     ABO     Aarburg-Oftringen    SBB  2016.0    2300.0    2700.0     2014.0   
3     AAT                Aathal    SBB  2016.0     690.0     750.0     2014.0   
4      AE                 Aesch    SBB  2016.0    1900.0    2200.0     2014.0   
5      AF    Affoltern am Albis    SBB  2016.0    6900.0    8100.0     2014.0   
6     AIG                 Aigle    CFF  2016.0    7600.0    8400.0     2014.0   
7      AI                Airolo    FFS  2016.0     550.0     490.0     2014.0   
8     ALL               Allaman    CFF  2016.0    3300.0    3900.0     2014.0   
9     ADF          Alpnach Dorf     ZB  2016.0    1500.0    1700.0     2014.0   
10    AST           Alpnachstad     ZB  2016.0     500.0     480.0     2014.0   
11     AL               Altdorf    SBB  2016.0     410.0     450.0     2014.0   
12   ALTD             Altendorf    SBB  2016.0     780.0     910.0     2014.0   
13     AT               Altmatt    SOB  2016.0      50.0      50.0     2014.0   
14    ALN                Altnau    SBB  2016.0     350.0     370.0     2014.0   
15    ALT         Altstätten SG    SBB  2016.0    2300.0    2600.0     2014.0   
16     AP          Ambri-Piotta    FFS  2016.0      50.0      50.0     2014.0   
17     AW              Amriswil    SBB  2016.0    3000.0    3400.0     2014.0   
18     AN           Andelfingen    SBB  2016.0    2300.0    2600.0     2014.0   
19    ARB                 Arbon    SBB  2016.0    1500.0    1700.0     2014.0   
20   ARBS     Arbon Seemoosriet    SBB  2016.0     410.0     460.0     2014.0   
21    ARD                 Ardon    CFF  2016.0     470.0     580.0     2014.0   
22    ARN                Arnegg    SBB  2016.0       0.0       0.0     2014.0   
23     AX                 Arnex    CFF  2016.0     200.0     230.0     2014.0   
24     GD           Arth-Goldau    SBB  2016.0   12600.0   12800.0     2014.0   
25   AUSG                 Au SG    SBB  2016.0     320.0     360.0     2014.0   
26     AU                 Au ZH    SBB  2016.0    1000.0    1200.0     2014.0   
27    AUV             Auvernier    CFF  2016.0     410.0     450.0     2014.0   
28     AV              Avenches    CFF  2016.0     710.0     830.0     2014.0   
29    BAA                  Baar    SBB  2016.0    8300.0    9800.0     2014.0   
..    ...                   ...    ...     ...       ...       ...        ...   
733  WUER              Würenlos    SBB  2016.0     920.0    1100.0     2014.0   
734   CHP  Yverdon-Champ Pittet    CFF  2016.0      50.0      60.0     2014.0   
735    YV     Yverdon-les-Bains    CFF  2016.0   16100.0   18900.0     2014.0   
736   YND               Yvonand    CFF  2016.0     620.0     730.0     2014.0   
737    ZB          Ziegelbrücke    SBB  2016.0    8900.0    9600.0     2014.0   
738   ZIM               Zimeysa    CFF  2016.0     930.0    1300.0     2014.0   
739    ZF              Zofingen    SBB  2016.0    8700.0   10100.0     2014.0   
740    ZK              Zollikon    SBB  2016.0    1100.0    1300.0     2014.0   
741    ZG                   Zug    SBB  2016.0   37500.0   43800.0     2014.0   
742  ZGCA            Zug Casino    SBB  2016.0     150.0     180.0     2014.0   
743  KMUE       Zug Chollermüli    SBB  2016.0     630.0     700.0     2014.0   
744  ZGFR          Zug Fridbach    SBB  2016.0     240.0     280.0     2014.0   
745   ZGO           Zug Oberwil    SBB  2016.0     250.0     280.0     2014.0   
746  ZGPP         Zug Postplatz    SBB  2016.0     140.0     160.0     2014.0   
747  ZGSE       Zug Schutzengel    SBB  2016.0    1200.0    1300.0     2014.0   
748   ZWD              Zweidlen    SBB  2016.0       0.0       0.0     2014.0   
749   ZWG               Zwingen    SBB  2016.0    2400.0    2800.0     2014.0   
750   ZAF      Zürich Affoltern    S

In [57]:
from bokeh.palettes import brewer

fig_2 = figure(x_range=data_passengers_on_change.Eigner)

# Get the number of colors we'll need for the plot.
colors = brewer["Spectral"][len(data_passengers_on_change.Eigner.unique())]

fig_2_plot = fig_2.circle(x = 'DTV_2016', y = 'DTV_2014', source = data_passengers_on_change)
show(fig_2)

In [58]:
# Get the number of colors we'll need for the plot.
colors = brewer["Spectral"][len(data_passengers_on_change.Eigner.unique())]
colors

['#3288bd', '#99d594', '#e6f598', '#fee08b', '#fc8d59', '#d53e4f']

In [59]:
gdf_loc_line

abkurzung_b              bezeichnung   linie     km  \
2539          LS                 Lausanne   100.0    0.0   
3351          LS                 Lausanne   100.0    0.0   
49            PU                    Pully   100.0    2.0   
1899         LTY                    Lutry   100.0    5.0   
3216         VTE              Villette VD   100.0    6.0   
1558          CU                    Cully   100.0    8.0   
791          EPS                  Epesses   100.0    9.0   
194          RIV                    Rivaz   100.0   13.0   
583         STSA              St-Saphorin   100.0   14.0   
1145          VV                    Vevey   100.0   17.0   
2374          VV                    Vevey   100.0   18.0   
2713        TOUR         La Tour-de-Peilz   100.0   19.0   
394         BURI                   Burier   100.0   21.0   
2427          CL                  Clarens   100.0   23.0   
2349          MX                 Montreux   100.0   24.0   
2707         TER                 Territet   100.0   26.0   
1138         VEY          Veytaux-Chillon   100.0   27.0   
2370         VIL               Villeneuve   100.0   29.0   
475          ROC                 Roche VD   100.0   33.0   
1609         AIG                    Aigle   100.0   39.0   
2281          ST               St-Triphon   100.0   43.0   
334          BEX                      Bex   100.0   47.0   
27           PDS               Les Paluds   100.0   50.0   
659           SM               St-Maurice   100.0   51.0   
796           EV                 Evionnaz   100.0   57.0   
2364        VERN                 Vernayaz   100.0   61.0   
2561          MA                 Martigny   100.0   66.0   
814         CHAR            Charrat-Fully   100.0   70.0   
1371         SAX                    Saxon   100.0   75.0   
1348         RID                   Riddes   100.0   79.0   
...          ...                      ...     ...    ...   
2147         LST                  Liestal  9501.0    8.0   
1737          OL                    Olten  9501.0   27.0   
2235         SAN              S. Antonino  9591.0  225.0   
2401        CAMO          Camorino (dira)  9591.0  227.0   
2906        FREU              Freudenberg  9668.0   46.0   
375         BRGL            Bruglen (Spw)  9668.0   48.0   
1722        NIDB          Nidelbad (Abzw)  9722.0   10.0   
2130        LITT             Litti (Baar)  9722.0   21.0   
2320        MEIB         Meilibach (Abzw)  9724.0    0.0   
1372         SBG                Sihlbrugg  9724.0    5.0   
1199        ZMUS  Zurich HB Museumstrasse  9728.0    0.0   
3085         ZTB     Zurich Tiefenbrunnen  9728.0    0.0   
3277        ZSTH       Zurich Stadelhofen  9728.0    0.0   
117         ZSTH       Zurich Stadelhofen  9729.0    0.0   
1459        ZHOT   Zurich Hottingen (Spw)  9729.0    0.0   
866          DTL                Dietlikon  9780.0   50.0   
3374        MBGW             Mulberg West  9780.0   54.0   
1112        TOEM                Tossmuhle  9780.0   59.0   
3155         DTL                Dietlikon  9781.0   50.0   
2315        MBGO              Mulberg Ost  9781.0   53.0   
1842        TOEM                Tossmuhle  9781.0   59.0   
702          BSD              Bassersdorf  9782.0   51.0   
2178        MBGW             Mulberg West  9782.0   54.0   
1503         BSD              Bassersdorf  9783.0   51.0   
2177        MBGO              Mulberg Ost  9783.0   53.0   
2681         BSD              Bassersdorf  9784.0   14.0   
2628        BALW        Baltenswil (Abzw)  9784.0   16.0   
919         SGAB             St.Gallen AB  9855.0    0.0   
1228        GBSG  St. Gallen Guterbahnhof  9855.0    0.0   
2207        RITH                Riethusli  9855.0    2.0   

                                 linienname verwaltung  \
2539   Lausanne - Simplon Tunnel I - Iselle    SBB CFF   
3351   Lausanne - Simplon Tunnel I - Iselle    SBB CFF   
49     Lausanne - Simplon Tunnel I - Iselle    SBB CFF   
1899   Lausanne - Simplon Tunnel I - Iselle    SBB C

In [65]:
row1 = row(menu, range_slider)

layout_hbar = column(row1, fig_hbar)

In [66]:
show(layout_hbar)

You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    http://bokeh.pydata.org/en/latest/docs/user_guide/interaction/callbacks.html

Alternatively, to use real Python callbacks, a Bokeh server application may
be used. For more information on building and running Bokeh applications, see:

    http://bokeh.pydata.org/en/latest/docs/user_guide/server.html



In [71]:
gdf_loc_line

abkurzung_b              bezeichnung   linie     km  \
2539          LS                 Lausanne   100.0    0.0   
3351          LS                 Lausanne   100.0    0.0   
49            PU                    Pully   100.0    2.0   
1899         LTY                    Lutry   100.0    5.0   
3216         VTE              Villette VD   100.0    6.0   
1558          CU                    Cully   100.0    8.0   
791          EPS                  Epesses   100.0    9.0   
194          RIV                    Rivaz   100.0   13.0   
583         STSA              St-Saphorin   100.0   14.0   
1145          VV                    Vevey   100.0   17.0   
2374          VV                    Vevey   100.0   18.0   
2713        TOUR         La Tour-de-Peilz   100.0   19.0   
394         BURI                   Burier   100.0   21.0   
2427          CL                  Clarens   100.0   23.0   
2349          MX                 Montreux   100.0   24.0   
2707         TER                 Territet   100.0   26.0   
1138         VEY          Veytaux-Chillon   100.0   27.0   
2370         VIL               Villeneuve   100.0   29.0   
475          ROC                 Roche VD   100.0   33.0   
1609         AIG                    Aigle   100.0   39.0   
2281          ST               St-Triphon   100.0   43.0   
334          BEX                      Bex   100.0   47.0   
27           PDS               Les Paluds   100.0   50.0   
659           SM               St-Maurice   100.0   51.0   
796           EV                 Evionnaz   100.0   57.0   
2364        VERN                 Vernayaz   100.0   61.0   
2561          MA                 Martigny   100.0   66.0   
814         CHAR            Charrat-Fully   100.0   70.0   
1371         SAX                    Saxon   100.0   75.0   
1348         RID                   Riddes   100.0   79.0   
...          ...                      ...     ...    ...   
2147         LST                  Liestal  9501.0    8.0   
1737          OL                    Olten  9501.0   27.0   
2235         SAN              S. Antonino  9591.0  225.0   
2401        CAMO          Camorino (dira)  9591.0  227.0   
2906        FREU              Freudenberg  9668.0   46.0   
375         BRGL            Bruglen (Spw)  9668.0   48.0   
1722        NIDB          Nidelbad (Abzw)  9722.0   10.0   
2130        LITT             Litti (Baar)  9722.0   21.0   
2320        MEIB         Meilibach (Abzw)  9724.0    0.0   
1372         SBG                Sihlbrugg  9724.0    5.0   
1199        ZMUS  Zurich HB Museumstrasse  9728.0    0.0   
3085         ZTB     Zurich Tiefenbrunnen  9728.0    0.0   
3277        ZSTH       Zurich Stadelhofen  9728.0    0.0   
117         ZSTH       Zurich Stadelhofen  9729.0    0.0   
1459        ZHOT   Zurich Hottingen (Spw)  9729.0    0.0   
866          DTL                Dietlikon  9780.0   50.0   
3374        MBGW             Mulberg West  9780.0   54.0   
1112        TOEM                Tossmuhle  9780.0   59.0   
3155         DTL                Dietlikon  9781.0   50.0   
2315        MBGO              Mulberg Ost  9781.0   53.0   
1842        TOEM                Tossmuhle  9781.0   59.0   
702          BSD              Bassersdorf  9782.0   51.0   
2178        MBGW             Mulberg West  9782.0   54.0   
1503         BSD              Bassersdorf  9783.0   51.0   
2177        MBGO              Mulberg Ost  9783.0   53.0   
2681         BSD              Bassersdorf  9784.0   14.0   
2628        BALW        Baltenswil (Abzw)  9784.0   16.0   
919         SGAB             St.Gallen AB  9855.0    0.0   
1228        GBSG  St. Gallen Guterbahnhof  9855.0    0.0   
2207        RITH                Riethusli  9855.0    2.0   

                                 linienname verwaltung  \
2539   Lausanne - Simplon Tunnel I - Iselle    SBB CFF   
3351   Lausanne - Simplon Tunnel I - Iselle    SBB CFF   
49     Lausanne - Simplon Tunnel I - Iselle    SBB CFF   
1899   Lausanne - Simplon Tunnel I - Iselle    SBB C